# Reading csv file into panda dataframes and converting dataframe into json file

In [ ]:
import pandas as pd
import json
df1 = pd.read_csv("E:/CS587/Food_Inspections.csv") # Reading the csv file into Panda Data Frame 

In [ ]:
s = df1.to_json(orient='records') # Converting the dataframe object into json records

In [ ]:
cont = json.loads(s) #Loading the json records into variable

For more information on elastic search visit https://www.elastic.co/webinars/getting-started-elasticsearch?elektra=home&storm=sub1

In [1]:
from elasticsearch import Elasticsearch, helpers #Improrting elasctic search and helpers of elastic search
es = Elasticsearch()

# Inserting the data into Elastic Search

Data is insreted into Elastic search using the bulk Api of elastic search. For more information visit the link http://elasticsearch-py.readthedocs.io/en/master/helpers.html

In [ ]:
### Inserting the data one by one in elastic search

# i =1
# for data in cont:
#    es.index(index='food_imspection_final_1', doc_type='food_inspection_doc_1', id=i, body=data)
#    i = i+1
# print(i)

In [ ]:

actions = []
for data in cont:
    action = {                                   # JSON file is read and stored in the list
        "_index": "food_inspection_2",
        "_type": "food",
        "_id": data['Inspection ID'],
        "_source": {
            "any":data
            }
        }
    actions.append(action)                      # Appending each record in the list

helpers.bulk(es, actions)                       #Inserting the list into elastci search

# Qurey to fetch all the data from elastic Search

In [2]:
doc = {
        'size' : 10000,
        'query': {
            'match_all' : {}
       }
   }
result_without_condition = es.search(index='food_inspection_2', body=doc,scroll='1h')

Only 10,000 records can be fetched at a time  https://www.elastic.co/guide/en/elasticsearch/reference/current/search-request-from-size.html.
Used the Scroll API of elastic search to fetch all the data matching the queries written in the previous cell. For more information visit https://www.elastic.co/guide/en/elasticsearch/reference/current/search-request-scroll.html

In [3]:
sid = result_without_condition['_scroll_id']
scroll_size = result_without_condition['hits']['total']

# Populating the data into local variable for all records

In [4]:
count = 0
final_location_ll = []
while(scroll_size > 0):

    for doc in result_without_condition['hits']['hits']:                   #Iterating each  results of  the qurey 
        location_ll = []
        results = doc['_source']['any']
        count = count +1
        if 'Latitude' in results.keys():
            if 'Longitude' in results.keys():
                if 'Address' in results.keys():
                    if(results['Latitude'] != None and results['Longitude'] != None  and results['Address'] != None): #Checking if the field dose not have null values of Latitude ,Longitude and Address fields.

                        
                        location_ll.append(float(results['Latitude']))    #Appending Latitude and Longitude into the list
                        location_ll.append(float(results['Longitude']))
                        final_location_ll.append(location_ll)
    result_without_condition = es.scroll(scroll_id = sid, scroll = '2m')    
    sid = result_without_condition['_scroll_id']                                 #Changing the scroll-id
    scroll_size = len(result_without_condition['hits']['hits'])  
print("the total number of records fetched",count)

the total number of records fetched 164953


# Qurey to fetched data matching certian conditions

Qurey is written to fetch the data from elastic search based in certain criteria. For more information how to write search queries visit the link https://www.elastic.co/guide/en/elasticsearch/reference/current/query-dsl-bool-query.html

In [5]:
doc1 = {
        'size' : 10000,
        'query': {
            'bool': {
                    'must' : [{'match' : {'any.Results': 'Fail'}},{'match' : {'any.Risk': 'Risk 1 (High)'}}, # same as where clasue in SQL
                        
                              {"query_string": {
                                            "query": "*hildren*",  #using regex of children  to match all posiible combintation of "Children"
                                            "fields": ["any.Facility Type","any.Violations","any.DBA Name"] #Multi-field matching query
                                             }
                            }
                              
           
                            ]              
                   }
                }
        }
result_with_condition = es.search(index='food_inspection_2', body=doc1,scroll='1h')

Used the Scroll API of elastic search to fetch all the data matching the queries written in the previous cell. For more information visit https://www.elastic.co/guide/en/elasticsearch/reference/current/search-request-scroll.html

In [6]:
sid = result_with_condition['_scroll_id']
scroll_size = result_with_condition['hits']['total']

# Populating the data into local variable

In [7]:
count = 0
final_location_ll_condition = []
while(scroll_size > 0):

    for doc in result_with_condition['hits']['hits']:                   #Iterating each  results of  the qurey 
        location_ll_condition = []
        results = doc['_source']['any']
        count = count +1
        if 'Latitude' in results.keys():
            if 'Longitude' in results.keys():
                if 'Address' in results.keys():
                    if(results['Latitude'] != None and results['Longitude'] != None  and results['Address'] != None): #Checking if the field dose not have null values of Latitude ,Longitude and Address fields.

                        
                        location_ll_condition.append(float(results['Latitude']))    #Appending Latitude and Longitude into the list
                        location_ll_condition.append(float(results['Longitude']))
                        final_location_ll_condition.append(location_ll_condition)
    result_with_condition = es.scroll(scroll_id = sid, scroll = '2m')    
    sid = result_with_condition['_scroll_id']                                 #Changing the scroll-id
    scroll_size = len(result_with_condition['hits']['hits'])  
print("the total number of match with children using wild card:",count)

the total number of match with children using wild card: 617


# Importing folium to plot the map

Generating Heat Map using Folium. For more information on generating heat map visit https://alysivji.github.io/getting-started-with-folium.html

For more information on folium visit https://github.com/python-visualization/folium

For more information about paramteres of HeatMap visit https://github.com/python-visualization/folium/blob/master/folium/plugins/heat_map.py

In [8]:
import folium
from folium import plugins


print(folium.__version__)

0.5.0


In [9]:
without_condition_heatmap = folium.Map([41.90293279, -87.70769386], 
               zoom_start=11)
without_condition_heatmap

# For generating HeatMap for all the records

In [10]:
without_condition_heatmap.add_child(plugins.HeatMap(final_location_ll[:40000], radius=15))
without_condition_heatmap

# For generating HeatMap records fetched on condtion

In [11]:
condition_heatmap = folium.Map([41.90293279, -87.70769386], 
               zoom_start=11)
condition_heatmap

In [12]:
condition_heatmap.add_child(plugins.HeatMap(final_location_ll_condition, radius=15))
condition_heatmap

# Using fuzziness

The fuzzy query generates all possible matching terms that are within the maximum edit distance specified in fuzziness.
To know about fuzziness visit  https://www.elastic.co/guide/en/elasticsearch/reference/current/query-dsl-fuzzy-query.html

In [13]:
doc = {
        'size' : 10000,
        'query': {
            'bool': {
                    'must' : [{'match' : {'any.Results': 'Fail'}},{'match' : {'any.Risk': 'Risk 1 (High)'}},
                            {"query_string": {
                                            "query": "Children's",
                                            "fuzziness": "1",
                                            "fields": ["any.Facility Type","any.Violations","any.DBA Name"]
                                             }
                            }
           
                            ]              
                   }
                }
        }
result_fuzziness = es.search(index='food_inspection_2', body=doc,scroll='1h')

In [14]:
sid = result_fuzziness['_scroll_id']
scroll_size = result_fuzziness['hits']['total']

# Populating the data into local variable¶


In [16]:
count = 0
final_location_ll_fuzziness = []
while(scroll_size > 0):

    for doc in result_fuzziness['hits']['hits']:
        location_ll_fuzziness = []
        results = doc['_source']['any']
        count = count +1
        if 'Latitude' in results.keys():
            if 'Longitude' in results.keys():
                if 'Address' in results.keys():
                    if(results['Latitude'] != None and results['Longitude'] != None  and results['Address'] != None):

                        
                        location_ll_fuzziness.append(float(results['Latitude']))
                        location_ll_fuzziness.append(float(results['Longitude']))
                        final_location_ll_fuzziness.append(location_ll_fuzziness)
    result_fuzziness = es.scroll(scroll_id = sid, scroll = '2m')
    sid = result_fuzziness['_scroll_id']
    scroll_size = len(result_fuzziness['hits']['hits'])  
print("the total number of match with children using fuziness:",count)

the total number of match with children using fuziness: 457


# Fuzziness HeatMap

In [19]:
fuzziness_heatmap = folium.Map([41.90293279, -87.70769386], 
               zoom_start=11)
fuzziness_heatmap

In [20]:
fuzziness_heatmap.add_child(plugins.HeatMap(final_location_ll_fuzziness, radius=15))
fuzziness_heatmap

# Query for aggregation function

In [31]:
doc = {
        'size' : 10000,
        'query': {
            'bool': {
                    'must' : [{'match' : {'any.Results': 'Fail'}},
                              {'match' : {'any.Risk': 'Risk 1 (High)'}}],
                    'should' : [{'match' : {'any.Facility Type': 'Daycare (2 - 6 Years)'}},
                                {'match' : {'any.Facility Type': 'Daycare Above and Under 2 Years'}},
                                {'match' : {'any.Facility Type': 'CHILDRENS SERVICES FACILITY'}},
                              ]              
                   }
                },
    "aggs" : {
        "selected_dbas" :{
                            "terms" : {
                                        "field" : "any.DBA Name.keyword",
                                         "min_doc_count": 5
                                       }
           
                        }
            
            }
    
        }

res_for_aggregation = es.search(index='food_inspection_2', body=doc,scroll='1h')

In [30]:
sid = res_for_aggregation['_scroll_id']
scroll_size = res_for_aggregation['hits']['total']

# Populating the data into local variable¶


In [24]:
count = 0
final_location_ll_aggregation = []
while(scroll_size > 0):

    for doc in res_for_aggregation['hits']['hits']:
        location_ll_aggregation = []
        results = doc['_source']['any']
        count = count +1
        if 'Latitude' in results.keys():
            if 'Longitude' in results.keys():
                if 'Address' in results.keys():
                    if(results['Latitude'] != None and results['Longitude'] != None  and results['Address'] != None):

                        
                        location_ll_aggregation.append(float(results['Latitude']))
                        location_ll_aggregation.append(float(results['Longitude']))
                        final_location_ll_aggregation.append(location_ll_aggregation)
    res_for_aggregation = es.scroll(scroll_id = sid, scroll = '2m')
    sid = res_for_aggregation['_scroll_id']
    scroll_size = len(res_for_aggregation['hits']['hits'])  
print("the total number of match with children using fuziness:",count)

the total number of match with children using fuziness: 31900


# Aggregation HeatMap

In [25]:
aggregation_heatmap = folium.Map([41.90293279, -87.70769386], 
               zoom_start=11)
aggregation_heatmap

In [26]:
aggregation_heatmap.add_child(plugins.HeatMap(final_location_ll_aggregation, radius=15))
aggregation_heatmap

In [32]:
res_for_aggregation

{'_scroll_id': 'DnF1ZXJ5VGhlbkZldGNoBQAAAAAAAACSFkhQYmExakRoU3I2bDdBeFB0dWNVaEEAAAAAAAAAkxZIUGJhMWpEaFNyNmw3QXhQdHVjVWhBAAAAAAAAAJQWSFBiYTFqRGhTcjZsN0F4UHR1Y1VoQQAAAAAAAACVFkhQYmExakRoU3I2bDdBeFB0dWNVaEEAAAAAAAAAlhZIUGJhMWpEaFNyNmw3QXhQdHVjVWhB',
 '_shards': {'failed': 0, 'skipped': 0, 'successful': 5, 'total': 5},
 'aggregations': {'selected_dbas': {'buckets': [{'doc_count': 281,
     'key': 'SUBWAY'},
    {'doc_count': 185, 'key': 'DUNKIN DONUTS'},
    {'doc_count': 102, 'key': "MCDONALD'S"},
    {'doc_count': 55, 'key': '7-ELEVEN'},
    {'doc_count': 50, 'key': 'MCDONALDS'},
    {'doc_count': 44, 'key': 'POTBELLY SANDWICH WORKS LLC'},
    {'doc_count': 40, 'key': 'CHIPOTLE MEXICAN GRILL'},
    {'doc_count': 38, 'key': "HAROLD'S CHICKEN SHACK"},
    {'doc_count': 37, 'key': 'CITGO'},
    {'doc_count': 29, 'key': "DOMINO'S PIZZA"}],
   'doc_count_error_upper_bound': 26,
   'sum_other_doc_count': 31039}},
 'hits': {'hits': [{'_id': '2078771',
    '_index': 'food_inspection_2',
    '_sc